In [ ]:
!pip install open3d

## Assignment 1

In [56]:
import numpy as np
from mpl_toolkits.mplot3d.art3d import Poly3DCollection
import matplotlib.pyplot as plt
import open3d as o3d

In [60]:
point_cloud = o3d.io.read_point_cloud("shoe_pc.ply")
print(point_cloud)
point_cloud = point_cloud.voxel_down_sample(voxel_size=0.03)
print(point_cloud)

PointCloud with 184803 points.
PointCloud with 7350 points.


In [61]:
o3d.visualization.draw_plotly([point_cloud])

## Re-orient

In [62]:
def orient_pc(point_cloud_to_be_oriented):
  point_cloud_to_be_oriented.estimate_normals()

  # Plane detection
  plane_model, inliers = point_cloud_to_be_oriented.segment_plane(distance_threshold=0.0001,
                                                  ransac_n=3,
                                                  num_iterations=1000)

  # Extract plane
  plane_cloud_oriented = point_cloud_to_be_oriented.select_by_index(inliers, invert=True)

  # # Orient plane along YZ plane
  plane_normal = point_cloud_to_be_oriented.normals[1]
  # print(plane_normal)

  x_axis = np.array([1, 0, 0])
  rotation_axis = np.cross(plane_normal, x_axis)
  rotation_angle = np.arccos(np.dot(plane_normal, x_axis))
  print("Axis ", rotation_axis)
  print("Angle ", rotation_angle)
  print("Plane center", plane_cloud_oriented.get_center())
  # rotation_matrix = o3d.geometry.get_rotation_matrix_from_xyz((0, rotation_angle, 0))
  rotation_matrix = o3d.geometry.get_rotation_matrix_from_xyz((0, rotation_angle, 0))
  plane_cloud_oriented.rotate(rotation_matrix, center=plane_cloud_oriented.get_center())

  return plane_cloud_oriented

plane_cloud = orient_pc(point_cloud)

# Visualize
o3d.visualization.draw_plotly([plane_cloud])

Axis  [ 0.          0.95112547 -0.06275704]
Angle  1.2636281892991224
Plane center [0.11875923 0.13930836 1.26105795]


In [63]:
def translate_pc(plane_cloud_to_be_translated):
  # Detect floor plane
  _, inliers = plane_cloud_to_be_translated.segment_plane(distance_threshold=0.01,
                                                  ransac_n=3,
                                                  num_iterations=1000)

  # Extract points from the floor plane
  floor_points = np.asarray(plane_cloud_to_be_translated.points)[inliers]

  # Centroid of the floor plane
  centroid = np.mean(floor_points, axis=0)

  # Translation vector to move the centroid to the origin
  translation_vector = -centroid
  print(translation_vector)

  # Translation to move the plane to the origin
  plane_cloud_to_be_translated.translate(translation_vector)

  return plane_cloud_to_be_translated

plane_cloud_translated = translate_pc(plane_cloud)

# Visualize the re-oriented point cloud
o3d.visualization.draw_plotly([plane_cloud_translated])

[-0.22036957 -0.15709004 -1.26090101]


## Visualize point cloud as mesh

In [64]:
distances = plane_cloud_translated.compute_nearest_neighbor_distance()
avg_dist = np.mean(distances)
radius = 3 * avg_dist
print(radius)

0.056486789714105506


In [66]:
def convert_pc_to_mesh(plane_cloud):
  plane_cloud.estimate_normals(search_param=o3d.geometry.KDTreeSearchParamHybrid(radius=radius, max_nn=100))
  poisson_mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(plane_cloud, depth=8, width=0, scale=1.1, linear_fit=False)[0]
  bbox = plane_cloud.get_axis_aligned_bounding_box()
  p_mesh_crop = poisson_mesh.crop(bbox)

  dec_mesh = p_mesh_crop.simplify_quadric_decimation(10000)
  dec_mesh.remove_degenerate_triangles()
  dec_mesh.remove_duplicated_triangles()
  dec_mesh.remove_duplicated_vertices()
  dec_mesh.remove_non_manifold_edges()

  # o3d.visualization.draw_geometries([poisson_mesh])
  return dec_mesh

In [67]:
dec_mesh = convert_pc_to_mesh(plane_cloud_translated)

# Visualize the mesh
o3d.visualization.draw_plotly([dec_mesh])

## Test

In [68]:
def apply_random_transformation(points):

  angle_1 = np.random.uniform(0, 2*np.pi)
  angle_2 = np.random.uniform(0, 2*np.pi)
  angle_3 = np.random.uniform(0, 2*np.pi)
  translation = np.random.uniform(-1, 1, size=3)
  print(translation)
  rotation_matrix = o3d.geometry.get_rotation_matrix_from_xyz((0, angle_2, 0))
  points.rotate(rotation_matrix, center=points.get_center())
  points.translate(translation)

  return points

In [75]:
point_cloud_test = o3d.io.read_point_cloud("shoe_pc.ply")
point_cloud_test = point_cloud_test.voxel_down_sample(voxel_size=0.03)
print(point_cloud_test)

pcd = apply_random_transformation(point_cloud_test)


PointCloud with 7350 points.
[ 0.8681952   0.29409812 -0.79188456]


In [76]:
o3d.visualization.draw_plotly([pcd])

In [77]:
oriented_pc = orient_pc(pcd)

Axis  [ 0.          0.96911185 -0.06275704]
Angle  1.8116206062756317
Plane center [0.9891721  0.43431327 0.46918271]


In [78]:
o3d.visualization.draw_plotly([oriented_pc])

In [79]:
pc_to_translate = oriented_pc
translated_pc = translate_pc(pc_to_translate)

[-1.09073402 -0.45148869 -0.46698993]


In [80]:
o3d.visualization.draw_plotly([translated_pc])

In [82]:
test_mesh = convert_pc_to_mesh(translated_pc)

# Visualize the mesh
o3d.visualization.draw_plotly([test_mesh])